In [1]:
import pandas as pd
import panel as pn
import os
from datetime import datetime
import param

pn.extension()


In [8]:
class Tabela(param.Parameterized):
    sel_tipazuriranje = param.Selector(objects=["Sel1", "Sel2"])
    num = param.Number(1, bounds=(0, None))
    action = param.Action(lambda x: x.param.trigger('action'), label='Update')
    df = param.DataFrame(doc="""
      The current dataframe of samples.""")
        
        
    def __init__(self, **param):
        super(Tabela, self).__init__(**param)
        
        self.Tab_row = pn.Column()
        for _ in range(self.num):
            self._add_tab()
            
        self.Generatedataframe() 
            
        
            
    def _add_tab(self):
                
        tabela = pn.widgets.FileInput(accept='.px')
        folder = pn.widgets.FileSelector('G:\\Mravka')
        dat = pn.widgets.DatePicker(name='Date')
        potvrda = pn.widgets.Checkbox(name='Confirm')
        txtDat = pn.pane.Str('', width=150, style={'font-size': '8pt', 'color':'#FF0000'})
         
        self.Tab_row.append(pn.Row(tabela, folder, pn.Column(dat, txtDat), potvrda))
        
        
     
    def _remove_tab(self):
        widget = self.Tab_row.pop(-1)
        
        [widget.param.unwatch(watcher) for watcher in widget.param._watchers]
        del widget
    
    
    @param.depends('num', watch=True)
    def _update_colors(self):
        while len(self.Tab_row) != self.num:
            if len(self.Tab_row) > self.num:
                self._remove_tab()
            elif len(self.Tab_row) < self.num:
                self._add_tab()
                
    def panel(self):
        return pn.Column(
            pn.Row(
                pn.Param(self, parameters=['sel_tipazuriranje', 'num'])),
            self.Tab_row,
            pn.Param(self, parameters=['action']),
            pn.Param(self, parameters=['df']))
            
            
    
    @param.depends('action', watch=True)
    def Generatedataframe(self, event=None):
        imefajl = []
        pateka = []
        datumi = []
        zaobjavuvanje = []
        zabeleska = []
        
        for i in self.Tab_row:
            if i[0].filename != None:
                fajl = i[0].filename
            else:
                fajl = ''
                
            if i[2][0].value != None:
                date_time_obj = datetime.strptime(str(i[2][0].value), '%Y-%m-%d')
                dat = datetime.strftime(date_time_obj, '%d-%m-%Y')
            else:
                dat = ''
                
            if i[1].value is not None and i[0].filename is not None:
                dest = os.path.join(i[1].value[0], i[0].filename)
            else:
                dest = ''
            
            imefajl.append(fajl)
            pateka.append(dest)
            datumi.append(dat)
            zaobjavuvanje.append(i[3].value)
            zabeleska.append('')
            
        tbl = {'a':imefajl,
           'b':pateka, 
           'c':datumi, 
           'd':zaobjavuvanje, 
           'e':zabeleska}
        
        self.df = pd.DataFrame(tbl)
        
        
        
            
    
            
        
c = Tabela()
c.panel().servable()

Column
    [0] Row
        [0] Param(Tabela, parameters=['sel_tipazuriranje', ...])
    [1] Column
        [0] Row
            [0] FileInput(accept='.px')
            [1] FileSelector(directory='G:\\Mravka')
            [2] Column
                [0] DatePicker(name='Date')
                [1] Str(str, style={'font-size': '8pt', ...}, width=150)
            [3] Checkbox(name='Confirm')
    [2] Param(Tabela, parameters=['action'])
    [3] Param(Tabela, parameters=['df'])

In [9]:
c.panel().show()

Launching server at http://localhost:63433
